Installing required libraries

In [35]:
pip install requests sqlalchemy beautifulsoup4 python-dotenv psycopg2 selenium 

In [2]:
!pip install selenium

In [3]:
import selenium
print(selenium.__version__)

4.28.1


In [4]:
!pip install webdriver-manager

Import required libraries

In [36]:
import pandas as pd
from sqlalchemy import create_engine, text
from bs4 import BeautifulSoup
import requests
from dotenv import load_dotenv
import os 
import re
from selenium import webdriver 
from selenium.webdriver.chrome.service import Service 
from selenium.webdriver.chrome.options import Options
from webdriver_manager.chrome import ChromeDriverManager
import time  

Data Extraction


In [43]:
options = Options()
options.headless = True

service = Service(ChromeDriverManager().install())

driver = webdriver.Chrome(service=service, options=options)
url = 'https://www.booking.com/searchresults.html?ss=london&efdco=1&label=gen173nr-1FCAEoggI46AdIM1gEaFCIAQGYATG4ARfIAQzYAQHoAQH4AQKIAgGoAgO4AqqI1LwGwAIB0gIkNjkyMzM1ZDEtNzUzZC00YzlmLWFiZTYtMWZiNjE4ZWUwZTAz2AIF4AIB&aid=304142&lang=en-us&sb=1&src_elem=sb&src=index&dest_id=-2601889&dest_type=city&place_id=city%2F-2601889&ac_position=0&ac_click_type=b&ac_langcode=en&ac_suggestion_list_length=5&search_selected=true&search_pageview_id=8fa56d55e5270165&ac_meta=GhA1NmEwNmQ2YjQ3OGQwM2U2IAAoATICZW46BmxvbmRvbkAASgBQAA%3D%3D&checkin=2025-01-25&checkout=2025-02-28&group_adults=2&no_rooms=1&group_children=0'

driver.get(url)

time.sleep(30)

page_source = driver.page_source


scroll_time = 10
last_height = driver.execute_script('return document.body.scrollHeight')
while True:
    # scroll down to the bottom
    driver.execute_script('window.scrollTo(0, document.body.scrollHeight);')

    time.sleep(scroll_time)
    # new height
    new_height = driver.execute_script('return document.body.scrollHeight')
    
    if new_height == last_height:
        break
    
    last_height = new_height
    
    
page_source = driver.page_source
print('successful')
driver.quit()

successful


In [44]:
soup = BeautifulSoup(page_source, 'html.parser')

In [45]:
soup

<html class="b_chrome b_chrome_131 supports_inline-block supports_flexbox_unprefixed supports_fontface hasJS" dir="ltr" lang="en-us" prefix="og: http://ogp.me/ns# fb: http://ogp.me/ns/fb# booking_com: http://ogp.me/ns/fb/booking_com#"><head><script src="https://ct.pinterest.com/static/ct/token_create.js"></script><script async="" class="optanon-category-C0004" src="https://s.pinimg.com/ct/lib/main.7d8116bd.js"></script><script async="" class="optanon-category-C0004" nonce="" src="https://www.googletagmanager.com/gtag/destination?id=AW-1060768846&amp;l=dataLayer&amp;cx=c&amp;gtm=45He51n0v79615461za200" type="text/javascript"></script><script async="" nonce="" src="https://s.yimg.jp/images/listing/tool/cv/ytag.js" type="text/javascript"></script><script async="" class="optanon-category-C0004" nonce="" src="https://www.googletagmanager.com/gtag/destination?id=AW-988382855&amp;l=dataLayer&amp;cx=c&amp;gtm=45He51n0v79615461za200" type="text/javascript"></script><script async="" class="optan

In [46]:
final_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 73 entries, 0 to 72
Data columns (total 5 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   name      73 non-null     object
 1   link      73 non-null     object
 2   location  73 non-null     object
 3   price     73 non-null     object
 4   rating    73 non-null     object
dtypes: object(5)
memory usage: 3.0+ KB


In [47]:
hotels =soup.find_all('div', {'data-testid' : 'property-card'})
hotels

[<div aria-label="Property" class="c82435a4b8 a178069f51 a6ae3c2b40 a18aeea94d d794b7a0f7 f53e278e95 c6710787a4" data-testid="property-card" role="listitem" style="--bui_box_spaced_padding--s: 4;"><div class="c066246e13 d8aec464ca" data-testid="property-card-container"><div class="a5922b8ca1"><div class="e952b01718 a3f1b35606"><a aria-hidden="true" data-testid="property-card-desktop-single-image" href="https://www.booking.com/hotel/gb/fivem-apartments-notting-hill.html?label=gen173nr-1FCAEoggI46AdIM1gEaFCIAQGYATG4ARfIAQzYAQHoAQH4AQKIAgGoAgO4AqqI1LwGwAIB0gIkNjkyMzM1ZDEtNzUzZC00YzlmLWFiZTYtMWZiNjE4ZWUwZTAz2AIF4AIB&amp;aid=304142&amp;ucfs=1&amp;arphpl=1&amp;checkin=2025-01-25&amp;checkout=2025-02-28&amp;dest_id=-2601889&amp;dest_type=city&amp;group_adults=2&amp;req_adults=2&amp;no_rooms=1&amp;group_children=0&amp;req_children=0&amp;hpos=1&amp;hapos=1&amp;sr_order=popularity&amp;srpvid=00c57ff5b3390424&amp;srepoch=1737828797&amp;all_sr_blocks=1267153003_399432320_0_0_0&amp;highlighted_bloc

In [53]:
hotels_data = []
for hotel in hotels:
    name_element = hotel.find('div', {'data-testid' : 'title'})
    name = name_element.text.strip() if name_element else 'N/A'
    
    link_element = hotel.find('a', {'data-testid' : 'title-link'})
    link = link_element['href'] if link_element else 'N/A'
    
    location_element =hotel.find('span', {'data-testid' : 'address'})
    location = location_element.text.strip() if location_element else 'N/A'
    
    price_element =hotel.find('span', {'data-testid' : 'price-and-discounted-price'})
    price = price_element.text.strip() if price_element else 'N/A'
    
    rating_element = hotel.find('div', {'data-testid' : 'review-score'})
    if rating_element:
        rating = rating_element.text.strip().split()[1]
    else: 
        rating = 'N/A'
    
    hotels_data.append({
        'name' : name,
        'link' : link,
        'location' : location,
        'price' : price,
        'rating' :rating 
         
    })
    

In [54]:
hotels_data

[{'name': 'FiveM Notting Hill',
  'link': 'https://www.booking.com/hotel/gb/fivem-apartments-notting-hill.html?label=gen173nr-1FCAEoggI46AdIM1gEaFCIAQGYATG4ARfIAQzYAQHoAQH4AQKIAgGoAgO4AqqI1LwGwAIB0gIkNjkyMzM1ZDEtNzUzZC00YzlmLWFiZTYtMWZiNjE4ZWUwZTAz2AIF4AIB&aid=304142&ucfs=1&arphpl=1&checkin=2025-01-25&checkout=2025-02-28&dest_id=-2601889&dest_type=city&group_adults=2&req_adults=2&no_rooms=1&group_children=0&req_children=0&hpos=1&hapos=1&sr_order=popularity&srpvid=00c57ff5b3390424&srepoch=1737828797&all_sr_blocks=1267153003_399432320_0_0_0&highlighted_blocks=1267153003_399432320_0_0_0&matching_block_id=1267153003_399432320_0_0_0&sr_pri_blocks=1267153003_399432320_0_0_0__536706&from=searchresults',
  'location': 'Kensington and Chelsea, London',
  'price': '£5,367',
  'rating': '8.5'},
 {'name': 'The Pelham London - Starhotels Collezione',
  'link': 'https://www.booking.com/hotel/gb/the-pelham.html?label=gen173nr-1FCAEoggI46AdIM1gEaFCIAQGYATG4ARfIAQzYAQHoAQH4AQKIAgGoAgO4AqqI1LwGwAIB0gIkN

In [55]:
final_data = pd.DataFrame(hotels_data)

In [56]:
final_data

name  \
0                                   FiveM Notting Hill   
1            The Pelham London - Starhotels Collezione   
2                                  AMANO Covent Garden   
3            Cheval Three Quays at The Tower of London   
4           Luxury Flat in Kensington - Central London   
..                                                 ...   
143                                Victoria Inn London   
144                             OYO London Guest House   
145  The Residence Fitzrovia - Private One Bedroom ...   
146                                  The Wesley Euston   
147                          London City Airport Hotel   

                                                  link  \
0    https://www.booking.com/hotel/gb/fivem-apartme...   
1    https://www.booking.com/hotel/gb/the-pelham.ht...   
2    https://www.booking.com/hotel/gb/amano-covent-...   
3    https://www.booking.com/hotel/gb/cheval-three-...   
4    https://www.booking.com/hotel/gb/luxury-flat-i...   
..                                                 ...   
143  https://www.booking.com/hotel/gb/victoriainn.h...   
144  https://www.booking.com/hotel/gb/londonguestho...   
145  https://www.booking.com/hotel/gb/the-residence...   
146  https://www.booking.com/hotel/gb/mic-and-confe...   
147  https://www.booking.com/hotel/gb/london-city-a...   

                           location    price rating  
0    Kensington and Chelsea, London   £5,367    8.5  
1    Kensington and Chelsea, London   £9,155    8.3  
2       Westminster Borough, London   £7,983    8.3  
3            City of London, London  £21,553    9.3  
4    Kensington and Chelsea, London  £10,458    9.5  
..                              ...      ...    ...  
143     Westminster Borough, London   £3,692    7.2  
144                   Acton, London   £2,542    7.6  
145     Westminster Borough, London   £8,829    8.8  
146                  Camden, London   £5,146    7.4  
147                  Newham, London   £2,991    7.4  

[148 rows x 5 columns]

Transformation


In [57]:
def clean_price(price):
    return price.replace('£', '').replace(',', '').strip()
final_data['price'] =  final_data['price'].apply(clean_price)

In [58]:
final_data.head()

name  \
0                          FiveM Notting Hill   
1   The Pelham London - Starhotels Collezione   
2                         AMANO Covent Garden   
3   Cheval Three Quays at The Tower of London   
4  Luxury Flat in Kensington - Central London   

                                                link  \
0  https://www.booking.com/hotel/gb/fivem-apartme...   
1  https://www.booking.com/hotel/gb/the-pelham.ht...   
2  https://www.booking.com/hotel/gb/amano-covent-...   
3  https://www.booking.com/hotel/gb/cheval-three-...   
4  https://www.booking.com/hotel/gb/luxury-flat-i...   

                         location  price rating  
0  Kensington and Chelsea, London   5367    8.5  
1  Kensington and Chelsea, London   9155    8.3  
2     Westminster Borough, London   7983    8.3  
3          City of London, London  21553    9.3  
4  Kensington and Chelsea, London  10458    9.5

load to database


In [59]:
load_dotenv(override=True)
db_user = os.getenv('DB_USER')
db_name = os.getenv('DB_NAME')
db_host = os.getenv('DB_HOST')
db_port = os.getenv('DB_PORT')
db_password = os.getenv('DB_PASSWORD')

In [60]:
db_name

'Lodgify'

In [61]:
database_url = f"postgresql+psycopg2://{db_user}:{db_password}@{db_host}:{db_port}/{db_name}"
engine = create_engine(database_url)

display('Connected successfully')



'Connected successfully'

In [62]:
final_data.to_sql('Hotel_data',engine, if_exists='replace', index=False)

148